In [1]:
!ls /kaggle/input/categorized-medical-waste-image-dataset/Dataset/Baackground_Removed


ampoules_full	       hemostats		uncategorized_or_overlapping
ampuoles_broken        human_organs		used_masks
blood_soaked_bandages  iv_bottles		used_medical_gloves
disinfectant_bottles   mayo_scissors		used_medical_paper
episiotomy_scissors    scalpels			used_syringes
expired_tablets        stitch_removal_scissors	vaccine_or_medicine_vials
forceps		       syrup_bottles		waterbottles
general_organic_waste  tweezers


In [2]:
COUNT = 100
TRAIN = '/kaggle/input/categorized-medical-waste-image-dataset/Dataset/Baackground_Removed'

In [3]:
import torch
import torchvision.models as models
import torchvision.transforms as transforms
import numpy as np


DEVICE = torch.device('cpu')
OUTPUT_SIZE = 2048

model = models.resnext50_32x4d(weights=models.ResNeXt50_32X4D_Weights.IMAGENET1K_V2)

extraction_layer = model._modules.get('avgpool')
model.to(DEVICE)
model.eval()

scaler = transforms.Resize((224, 224))
normalize = transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
to_tensor = transforms.ToTensor()

def get_vec(arg, model, extraction_layer):
    image = normalize(to_tensor(scaler(arg))).unsqueeze(0).to(DEVICE)
    result = torch.zeros(1, OUTPUT_SIZE, 1, 1)
    def copy_data(m, i, o):
        result.copy_(o.data)
    hooked = extraction_layer.register_forward_hook(copy_data)
    with torch.no_grad():
        model(image)
    hooked.remove()
    return result

Downloading: "https://download.pytorch.org/models/resnext50_32x4d-1a0047aa.pth" to /root/.cache/torch/hub/checkpoints/resnext50_32x4d-1a0047aa.pth
100%|██████████| 95.8M/95.8M [00:01<00:00, 60.7MB/s]


In [4]:
import arrow
import base64
import pandas as pd
from glob import iglob
from io import BytesIO
from os.path import basename
from PIL import Image

THUMBNAIL_SIZE = (64, 64)

def embed(model, filename: str):
    with Image.open(fp=filename, mode='r') as image:
        return get_vec(arg=image.convert('RGB'), model=model, extraction_layer=extraction_layer).numpy().reshape(OUTPUT_SIZE,)


# https://stackoverflow.com/a/952952
def flatten(arg):
    return [x for xs in arg for x in xs]

def png(filename: str) -> str:
    with Image.open(fp=filename, mode='r') as image:
        buffer = BytesIO()
        # our images are pretty big; let's shrink the hover images to thumbnail size
        image.resize(size=THUMBNAIL_SIZE).convert('RGB').save(buffer, format='png')
        return 'data:image/png;base64,' + base64.b64encode(buffer.getvalue()).decode()

def get_picture_from_glob(arg: str, tag: str,) -> list:
    time_get = arrow.now()
    result = [pd.Series(data=[tag, basename(input_file), embed(model=model, filename=input_file), png(filename=input_file)],
                        index=['tag', 'name', 'value', 'png'])
        for index, input_file in enumerate(list(iglob(pathname=arg))) if index < COUNT]
    print('encoded {} rows of {}  in {}'.format(len(result), tag, arrow.now() - time_get))
    return result

time_start = arrow.now()
train_dict = {basename(folder) : folder + '/*.*' for folder in iglob(TRAIN + '/*')}
train_df = pd.DataFrame(data=flatten(arg=[get_picture_from_glob(arg=value, tag=key) for key, value in train_dict.items()]))

print('done in {}'.format(arrow.now() - time_start))

encoded 100 rows of ampoules_full  in 0:00:14.190959
encoded 100 rows of iv_bottles  in 0:01:43.908004
encoded 100 rows of stitch_removal_scissors  in 0:00:15.617638
encoded 100 rows of used_medical_paper  in 0:00:17.896487
encoded 100 rows of used_syringes  in 0:00:15.645006
encoded 100 rows of hemostats  in 0:00:16.283325
encoded 100 rows of general_organic_waste  in 0:00:16.205399
encoded 100 rows of forceps  in 0:00:15.861676
encoded 100 rows of waterbottles  in 0:00:22.472240
encoded 100 rows of tweezers  in 0:00:19.075261
encoded 100 rows of disinfectant_bottles  in 0:00:14.179495
encoded 100 rows of blood_soaked_bandages  in 0:00:20.720607
encoded 100 rows of vaccine_or_medicine_vials  in 0:00:14.319938
encoded 100 rows of syrup_bottles  in 0:00:14.216579
encoded 100 rows of used_medical_gloves  in 0:00:17.549083
encoded 100 rows of mayo_scissors  in 0:00:15.907440
encoded 100 rows of uncategorized_or_overlapping  in 0:00:17.145722
encoded 100 rows of scalpels  in 0:00:15.365763

In [5]:
train_df['tag'].value_counts().to_frame().T

tag    ampoules_full  vaccine_or_medicine_vials  ampuoles_broken  \
count            100                        100              100   

tag    expired_tablets  human_organs  episiotomy_scissors  scalpels  \
count              100           100                  100       100   

tag    uncategorized_or_overlapping  mayo_scissors  used_medical_gloves  ...  \
count                           100            100                  100  ...   

tag    disinfectant_bottles  tweezers  waterbottles  forceps  \
count                   100       100           100      100   

tag    general_organic_waste  hemostats  used_syringes  used_medical_paper  \
count                    100        100            100                 100   

tag    stitch_removal_scissors  used_masks  
count                      100         100  

[1 rows x 23 columns]

In [6]:
from sklearn.manifold import TSNE

train_reducer = TSNE(random_state=2025, verbose=True, n_jobs=1, perplexity=20.0, init='pca')
train_df[['x', 'y']] = train_reducer.fit_transform(X=train_df['value'].apply(func=pd.Series))

[t-SNE] Computing 61 nearest neighbors...
[t-SNE] Indexed 2300 samples in 0.011s...
[t-SNE] Computed neighbors for 2300 samples in 0.549s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2300
[t-SNE] Computed conditional probabilities for sample 2000 / 2300
[t-SNE] Computed conditional probabilities for sample 2300 / 2300
[t-SNE] Mean sigma: 4.114557
[t-SNE] KL divergence after 250 iterations with early exaggeration: 73.622574
[t-SNE] KL divergence after 1000 iterations: 0.975166


In [7]:
from bokeh.models import ColumnDataSource
from bokeh.models import HoverTool

from bokeh.plotting import figure
from bokeh.plotting import output_notebook
from bokeh.plotting import show
from bokeh.palettes import Turbo256
from bokeh.transform import factor_cmap

output_notebook()

datasource = ColumnDataSource(train_df[['png', 'tag', 'x', 'y']])
factor_count = max(train_df['tag'].nunique(), 3)
indices = np.linspace(0, len(Turbo256)-1, factor_count, dtype=int)
palette = [Turbo256[index] for index in indices]
mapper = factor_cmap(field_name = 'tag', palette=palette, factors=train_df['tag'].unique().tolist(), start=0, end=factor_count-1, )

plot_figure = figure(title='TSNE projection: medical waste', width=1000, height=800, tools=('pan, wheel_zoom, reset'))

plot_figure.add_tools(HoverTool(tooltips="""
<div>
    <div>
        <img src='@png' style='float: left; margin: 5px 5px 5px 5px'/>
    </div>
    <div>
        <span style='font-size: 18px'>@tag</span>
    </div>
</div>
"""))

plot_figure.scatter(x='x', y='y', source=datasource, line_alpha=0.6, fill_alpha=0.6, size=8, color=mapper)
show(plot_figure)

Loading BokehJS ...

In [8]:
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report
from sklearn.metrics import f1_score
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(train_df['value'].apply(pd.Series), train_df['tag'], test_size=0.25, random_state=2025, stratify=train_df['tag'])
logreg = LogisticRegression(max_iter=10000, tol=1e-12).fit(X_train, y_train)
print('model fit in {} iterations'.format(logreg.n_iter_[0]))
print('accuracy: {:5.4f}'.format(accuracy_score(y_true=y_test, y_pred=logreg.predict(X=X_test))))
print('f1: {:5.4f}'.format(f1_score(average='weighted', y_true=y_test, y_pred=logreg.predict(X=X_test))))
print(classification_report(y_true=y_test, y_pred=logreg.predict(X=X_test)))

model fit in 350 iterations
accuracy: 0.9026
f1: 0.9022
                              precision    recall  f1-score   support

               ampoules_full       0.84      0.84      0.84        25
             ampuoles_broken       0.79      0.76      0.78        25
       blood_soaked_bandages       0.93      1.00      0.96        25
        disinfectant_bottles       1.00      0.76      0.86        25
         episiotomy_scissors       0.82      0.92      0.87        25
             expired_tablets       0.74      0.80      0.77        25
                     forceps       1.00      1.00      1.00        25
       general_organic_waste       0.92      0.96      0.94        25
                   hemostats       0.93      1.00      0.96        25
                human_organs       0.91      0.84      0.87        25
                  iv_bottles       1.00      1.00      1.00        25
               mayo_scissors       0.91      0.80      0.85        25
                    scalpels     